In [ ]:
!pip install cdsapi

# Import libraries

In [ ]:
from google.colab import userdata
from google.colab import drive
import sys
import openai
import os
import subprocess
import openeo

# drive.mount('/content/drive')
# sys.path.append('/content/drive/MyDrive/Credentials/')

# 1.Define username and password credentials

In [ ]:
production = 'https://umm-api.apps.eo4eu.eu'

username = userdata.get('username')
password = userdata.get('password')
env = production

username

'kakiap'

### 1.1 Create token

In [ ]:
token, refresh = openeo.get_token(env, username, password, otp)

### 1.2 Refresh token - Super Useful

In [ ]:
token, refresh = openeo.refresh_token(env, refresh)

# 2. List workflows

In [ ]:
status = openeo.status_type.PUBLISHED #STOPPED
cfs = openeo.cfs_type.FALSE
workflows = openeo.list_workflows(env, status.value, cfs.value, token)

workflows

[('uc7_10_06', '228ec69a-6547-4680-b7a6-1001a259d4b8'),
 ('uc2_wind_v3', 'c2da80e8-15ba-4537-8c5e-5d96c607569a')]

# 3. Search workflow by name

In [ ]:
workflow_name = 'uc2_wind_v1'
status = openeo.status_type.STOPPED
cfs = openeo.cfs_type.FALSE
workflow_id = openeo.get_workflow_id(env, workflow_name, status.value, cfs.value, token)

print(workflow_id)

None


# 4. Get UC2-based script



In [ ]:
from pathlib import Path

file_path = Path("shub-8.py")
script_text = file_path.read_text()

print(script_text)

import os
import requests
import json
from datetime import datetime, timedelta

# Get the access token from the environment variable
access_token = os.getenv('ACCESS_TOKEN')
if not access_token:
    raise ValueError("ACCESS_TOKEN environment variable not set")

url = "https://services.sentinel-hub.com/api/v1/process"
headers = {
    "Authorization": f"Bearer {access_token}"
}

# Define the bounding box and other static parameters
bounds = {
    "bbox": [1247452.3364014172, 5152152.990191021, 1386873.4307700356, 5227700.6990901455],
    "properties": {
        "crs": "http://www.opengis.net/def/crs/EPSG/0/3857"
    }
}

output = {
    "width": 1000,
    "height": 1000,
    "responses": [
        {
            "identifier": "default",
            "format": {
                "type": "image/tiff"
            }
        }
    ]
}

evalscript = """//VERSION=3
function setup() {
    return {
        input: ["VH", "dataMask"],
        output: { 
            id: "default", 
            bands: 1,

# 5. Workflow actions

### 5.1 Encode the script in base64

In [ ]:
import base64

script_string_bytes = script_text.encode("ascii")
base64_bytes_script = base64.b64encode(script_string_bytes)
base64_string_script = base64_bytes_script.decode("ascii")

print(f"Encoded string: {base64_string_script}")

Encoded string: aW1wb3J0IG9zCmltcG9ydCByZXF1ZXN0cwppbXBvcnQganNvbgpmcm9tIGRhdGV0aW1lIGltcG9ydCBkYXRldGltZSwgdGltZWRlbHRhCgojIEdldCB0aGUgYWNjZXNzIHRva2VuIGZyb20gdGhlIGVudmlyb25tZW50IHZhcmlhYmxlCmFjY2Vzc190b2tlbiA9IG9zLmdldGVudignQUNDRVNTX1RPS0VOJykKaWYgbm90IGFjY2Vzc190b2tlbjoKICAgIHJhaXNlIFZhbHVlRXJyb3IoIkFDQ0VTU19UT0tFTiBlbnZpcm9ubWVudCB2YXJpYWJsZSBub3Qgc2V0IikKCnVybCA9ICJodHRwczovL3NlcnZpY2VzLnNlbnRpbmVsLWh1Yi5jb20vYXBpL3YxL3Byb2Nlc3MiCmhlYWRlcnMgPSB7CiAgICAiQXV0aG9yaXphdGlvbiI6IGYiQmVhcmVyIHthY2Nlc3NfdG9rZW59Igp9CgojIERlZmluZSB0aGUgYm91bmRpbmcgYm94IGFuZCBvdGhlciBzdGF0aWMgcGFyYW1ldGVycwpib3VuZHMgPSB7CiAgICAiYmJveCI6IFsxMjQ3NDUyLjMzNjQwMTQxNzIsIDUxNTIxNTIuOTkwMTkxMDIxLCAxMzg2ODczLjQzMDc3MDAzNTYsIDUyMjc3MDAuNjk5MDkwMTQ1NV0sCiAgICAicHJvcGVydGllcyI6IHsKICAgICAgICAiY3JzIjogImh0dHA6Ly93d3cub3Blbmdpcy5uZXQvZGVmL2Nycy9FUFNHLzAvMzg1NyIKICAgIH0KfQoKb3V0cHV0ID0gewogICAgIndpZHRoIjogMTAwMCwKICAgICJoZWlnaHQiOiAxMDAwLAogICAgInJlc3BvbnNlcyI6IFsKICAgICAgICB7CiAgICAgICAgICAgICJpZGVudGlmaWVyIjogImRlZmF1

### 5.2 Create a draft workflow with input of UC1


In [ ]:
workflow_name = 'uc2_wind_v1'
data = {
    "name": workflow_name,
    "query": [
        base64_string_script
    ],
    "meta": " "
}
status, text = openeo.workflow_create(env, data, token)

print(status, text)

201 New Message Recorded!


**If it is our first time, we need to go to the Workflow editor to create the workflow schema**


### 5.3 Start a workflow

In [ ]:
workflow_name = 'uc2_wind_v1'
workflow_id = openeo.get_workflow_id(env, workflow_name, 'DRAFT', 'false', token)
status, text = openeo.workflow_start(env, workflow_id, token)

print(status, text)
print(workflow_id)

202 
e4727cbb-f53f-4d21-b32f-105320b1a733


### 5.4 Stop workflow

In [ ]:
status, text = openeo.workflow_stop(env, workflow_id, token)

print(status, text)

202 {"message":"Workflow stopped successfully"}


### 5.5 Restart workflow

In [ ]:
status, text = openeo.workflow_start(env, workflow_id, token)

print(status, text)

502 "Problem with the DSL server: BadRequest - {\"message\":\"You can start only workflows with status DRAFT or STOPPED\"}"


### 5.6 Update workflow

In [ ]:
import re
import base64

def update_dates(script:str, start_date:str, end_date:str):
    script = re.sub(r'start\_date = datetime\.strptime\("(.*?)", ".*?"\)', f"start_date = datetime.strptime(\"{start_date}\", \"%Y-%m-%dT%H:%M:%SZ\")", script)
    script = re.sub(r'end\_date = datetime\.strptime\("(.*?)", ".*?"\)', f"end_date = datetime.strptime(\"{end_date}\", \"%Y-%m-%dT%H:%M:%SZ\")", script)
    return script

start_date = '2020-12-31T22:00:00Z'
end_date = '2021-01-14T22:00:00Z'

updated_script = update_dates(script_text, start_date, end_date)
script_string_bytes = updated_script.encode("ascii")
base64_bytes_script = base64.b64encode(script_string_bytes)
base64_string_script = base64_bytes_script.decode("ascii")

print(f"Encoded string: {base64_string_script}")

Encoded string: aW1wb3J0IG9zCmltcG9ydCByZXF1ZXN0cwppbXBvcnQganNvbgpmcm9tIGRhdGV0aW1lIGltcG9ydCBkYXRldGltZSwgdGltZWRlbHRhCgojIEdldCB0aGUgYWNjZXNzIHRva2VuIGZyb20gdGhlIGVudmlyb25tZW50IHZhcmlhYmxlCmFjY2Vzc190b2tlbiA9IG9zLmdldGVudignQUNDRVNTX1RPS0VOJykKaWYgbm90IGFjY2Vzc190b2tlbjoKICAgIHJhaXNlIFZhbHVlRXJyb3IoIkFDQ0VTU19UT0tFTiBlbnZpcm9ubWVudCB2YXJpYWJsZSBub3Qgc2V0IikKCnVybCA9ICJodHRwczovL3NlcnZpY2VzLnNlbnRpbmVsLWh1Yi5jb20vYXBpL3YxL3Byb2Nlc3MiCmhlYWRlcnMgPSB7CiAgICAiQXV0aG9yaXphdGlvbiI6IGYiQmVhcmVyIHthY2Nlc3NfdG9rZW59Igp9CgojIERlZmluZSB0aGUgYm91bmRpbmcgYm94IGFuZCBvdGhlciBzdGF0aWMgcGFyYW1ldGVycwpib3VuZHMgPSB7CiAgICAiYmJveCI6IFsxMjQ3NDUyLjMzNjQwMTQxNzIsIDUxNTIxNTIuOTkwMTkxMDIxLCAxMzg2ODczLjQzMDc3MDAzNTYsIDUyMjc3MDAuNjk5MDkwMTQ1NV0sCiAgICAicHJvcGVydGllcyI6IHsKICAgICAgICAiY3JzIjogImh0dHA6Ly93d3cub3Blbmdpcy5uZXQvZGVmL2Nycy9FUFNHLzAvMzg1NyIKICAgIH0KfQoKb3V0cHV0ID0gewogICAgIndpZHRoIjogMTAwMCwKICAgICJoZWlnaHQiOiAxMDAwLAogICAgInJlc3BvbnNlcyI6IFsKICAgICAgICB7CiAgICAgICAgICAgICJpZGVudGlmaWVyIjogImRlZmF1

In [ ]:
data = {
    "query": [
        base64_string_script
    ],
    "meta": " "
}
status, text = openeo.workflow_update_dsl(workflow_id, data, token)
# status, text = openeo.workflow_update(env, workflow_id, data, token) # wait for EBOS to fix it

print(status, text)

200 


### 5.7 Delete workflow

In [ ]:
status, text = openeo.workflow_delete(env, workflow_id, token)

print(status, text)

500 


#4 List S3 bucket contents

In [ ]:
workflow_name = 'uc2_wind_v1'
status = openeo.status_type.PUBLISHED
cfs = openeo.cfs_type.FALSE
workflow_id = openeo.get_workflow_id(env, workflow_name, status.value, cfs.value, token)
content = openeo.list_s3_bucket(env, workflow_id, token)
print(workflow_id)
print(content)